In [3]:
import pandas as pd
import numpy as np
import statsmodels.formula.api as smf
!pip install pycountry
import pycountry

# STEP 1: Load GDP
gdp_raw = pd.read_csv('/content/GDPPC.csv')
gdp = gdp_raw.melt(id_vars=['geoUnit'], var_name='year', value_name='gdp_per_capita')
gdp['year'] = gdp['year'].str.extract(r'(\d{4})')
gdp = gdp.dropna(subset=['year'])
gdp['year'] = gdp['year'].astype(int)
gdp['gdp_per_capita'] = pd.to_numeric(gdp['gdp_per_capita'], errors='coerce')
gdp = gdp.rename(columns={'geoUnit': 'country'})  # 💡 Rename for merge

# STEP 2: Load cultural exports
exports_raw = pd.read_csv('/content/culture_exports.csv')
exports = exports_raw.rename(columns={'geoUnit': 'country', 'value': 'cultural_exports'})
exports = exports[['country', 'year', 'cultural_exports']]
exports['year'] = pd.to_numeric(exports['year'], errors='coerce')
exports['cultural_exports'] = pd.to_numeric(exports['cultural_exports'], errors='coerce')

# STEP 3: Load democracy
vdem_raw = pd.read_csv('/content/V-Dem-CY-Core-v15.csv')
vdem = vdem_raw[['country_name', 'year', 'v2x_libdem', 'v2x_polyarchy', 'v2x_partipdem']].copy()

# STEP 4: Convert country name to ISO3 code
def get_iso3(name):
    try:
        return pycountry.countries.lookup(name).alpha_3
    except:
        return np.nan

vdem['country'] = vdem['country_name'].apply(get_iso3)
vdem = vdem.dropna(subset=['country'])
vdem['year'] = pd.to_numeric(vdem['year'], errors='coerce')

# ✅ Print to verify
print("✅ GDP sample:\n", gdp.head())
print("✅ Exports sample:\n", exports.head())
print("✅ Democracy sample:\n", vdem.head())

# STEP 5: Merge all
df = exports.merge(gdp, on=['country', 'year'], how='inner')
df = df.merge(vdem, on=['country', 'year'], how='inner')
df = df.dropna()

# STEP 6: Transform
df['log_exports'] = np.log1p(df['cultural_exports'])
df['log_gdp'] = np.log1p(df['gdp_per_capita'])

# STEP 7: Regression
democracy_variable = 'v2x_partipdem'  # Change to v2x_polyarchy or v2x_partipdem as needed
formula = f'log_exports ~ {democracy_variable} + C(year)'

model = smf.ols(formula=formula, data=df).fit(cov_type='HC3')
print("\n✅ Regression Results:\n")
print(model.summary())


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 50.0 MB/s eta 0:00:00
✅ GDP sample:
     country  year  gdp_per_capita
813     AFG  1990             NaN
814     ALB  1990      617.230435
815     DZA  1990     2445.183327
816     ASM  1990             NaN
817     AND  1990    19563.657470
✅ Exports sample:
   country  year  cultural_exports
0     ABW  2005           0.54913
1     ABW  2009           0.98566
2     ABW  2010           3.19451
3     ABW  2011           4.45087
4     ABW  2012           2.66763
✅ Democracy sample:
   country_name  year  v2x_libdem  v2x_polyarchy  v2x_partipdem country
0       Mexico  1789       0.044          0.028          0.006     MEX
1       Mexico  1790       0.044          0.028          0.006     MEX
2       Mexico  1791       0.044          0.028          0.006     MEX
3       Mexico  1792       0.044          0.028          0.006     MEX
4       Mexico  1793       0.044          0.028          0.006     MEX

✅ Regression Results:

          

/tmp/ipython-input-3-1675721194.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vdem['year'] = pd.to_numeric(vdem['year'], errors='coerce')
